In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.font_manager as fm
import matplotlib as mpl
import torch
import random
import os
import json
from tqdm import tqdm
from collections import defaultdict

In [2]:
with open('./japanese_characters.txt', 'r') as f:
  chars = f.read()

kanji_chars = chars[92:]

font_dirs = ['../all-fonts', ]
font_files = fm.findSystemFonts(fontpaths=font_dirs)
font_list = fm.createFontList(font_files)
fm.fontManager.ttflist.extend(font_list)

/var/folders/8h/gq3wkjn971g716fqf8xqlpch0000gn/T/ipykernel_47222/1971218514.py:8: MatplotlibDeprecationWarning: 
The createFontList function was deprecated in Matplotlib 3.2 and will be removed two minor releases later. Use FontManager.addfont instead.
  font_list = fm.createFontList(font_files)


In [3]:
# num = 4
# trial = 1000000
# top = 100
# style_name = 'BIZUDPMincho-Regular'
# result_dir_path = f'../statistic/loss_dictionary/{style_name}'
# result_file_path = os.path.join(result_dir_path, f'{num}_{trial}.json')
# with open(result_file_path, 'r') as f:
#     result_info = json.load(f)

In [4]:
# ranking_info = defaultdict(int)
# ranking_count = defaultdict(int)
# ranking_ratio = defaultdict(float)

In [5]:
# for key in list(result_info.keys())[:top]:
#     loss_min_index = result_info[key]['loss_min_index']
#     for i, char in enumerate(key):
#         ranking_count[char] += 1
#         count = 0
#         for index in loss_min_index:
#             if index == i:
#                 count += 1
#         ranking_info[char] += count
# for key in ranking_info.keys():
#     ranking_ratio[key] = ranking_info[key] / ranking_count[key]

In [6]:
# sorted_ranking_ratio = {key: value for key, value in sorted(list(ranking_ratio.items()), key = lambda x: -x[1])}

In [3]:
def search_more(style_font_path, num, top, trial, before_trial=1000000):
    style_name = os.path.splitext(os.path.basename(style_font_path))[0]
    
    result_dir_path = f'../statistic/loss_dictionary/{style_name}'
    result_file_path = os.path.join(result_dir_path, f'{num}_{before_trial}.json')
    with open(result_file_path, 'r') as f:
        result_info = json.load(f)
        
    ranking_info = defaultdict(int)
    ranking_count = defaultdict(int)
    ranking_ratio = defaultdict(float)
    for key in list(result_info.keys())[:top]:
        loss_min_index = result_info[key]['loss_min_index']
        for i, char in enumerate(key):
            ranking_count[char] += 1
            count = 0
            for index in loss_min_index:
                if index == i:
                    count += 1
            ranking_info[char] += count
    for key in ranking_info.keys():
        ranking_ratio[key] = ranking_info[key] / ranking_count[key]
    
    sorted_ranking_ratio = {key: value for key, value in sorted(list(ranking_ratio.items()), key = lambda x: -x[1])}
    
    
    
    with open(f'../statistic/loss_dictionary/{style_name}_kanji.json', 'r') as f:
        all_loss_info = json.load(f)

    columns = list(sorted_ranking_ratio.keys())
    columns_number = [kanji_chars.index(column) for column in columns]
    index = list(kanji_chars)

    data = np.zeros((len(index), len(columns)))
    for i in range(len(columns)):
        tmp_column = [info['L1'] for info in list(all_loss_info[columns[i]].values())]
        data[:, i] = tmp_column

    result_info = {}
    indexes = [0] * num
    marked_set = set()
    for i in tqdm(range(trial)):
      while True:
        for i in range(num):
#           indexes[i] = columns_number[random.randint(0, len(columns) - 1)]
            indexes[i] = random.randint(0, len(columns) - 1)
        sorted_indexed = sorted(indexes)
        if tuple(sorted_indexed) not in marked_set:
          marked_set.add(tuple(sorted_indexed))
          break
      result = {}
      chars = ''
      for i in range(num):
        chars += index[columns_number[sorted_indexed[i]]]
      tmp_data = data[:, sorted_indexed]
      loss_amount = tmp_data.min(axis=1).sum()
      loss_min_index = tmp_data.argmin(axis=1, )

      result['index'] = [columns_number[index] for index in indexes]
      result['loss_amount'] = loss_amount
      result['loss_min_index'] = [int(l) for l in loss_min_index]
      result_info[chars] = result
    
    sorted_result_info = {
      key: value for key, value in sorted(result_info.items(), key=lambda item: item[1]['loss_amount'])
    }
    top_bottom_result_info = {}
    top_keys = list(sorted_result_info.keys())[:top]
    top_values = list(sorted_result_info.values())[:top]
    for key, value in zip(top_keys, top_values):
        top_bottom_result_info[key] = value

    result_dir_path = f'../statistic/loss_dictionary/{style_name}'
    result_file_path = os.path.join(result_dir_path, f'more_{num}_{trial}.json')
    if not os.path.exists(result_dir_path):
      os.makedirs(result_dir_path)
    with open(result_file_path, 'w') as f:
      json.dump(top_bottom_result_info, f)

In [4]:
# style_font_paths = [
#     # 'BIZUDPMincho-Regular.ttf',
# #     '851H-kktt_004.ttf',
# #     'JP_NotoSerifJP-Regular.otf',
#     '03スマートフォントUI.otf',
#     'Corporate-Logo-Rounded-Bold-ver3.otf',
#     '851CHIKARA-DZUYOKU_kanaA_004.ttf',
#     'JK-Maru-Gothic-M.otf',
# ]
# for style_font_path in style_font_paths:
#     num = 4
#     trial = 1000000
#     top = 100
#     search_more(style_font_path, num, top, trial)

In [5]:
style_font_path = '../fonts/BIZUDPMincho-Regular'
num = 4
trial = 1000000
top = 100
style_name = os.path.splitext(os.path.basename(style_font_path))[0]
result_dir_path = f'../statistic/loss_dictionary/{style_name}'
result_file_path = os.path.join(result_dir_path, f'more_{num}_{trial}.json')
with open(result_file_path, 'r') as f:
    result_info = json.load(f)

In [6]:
result_info

{'爆興薪妥': {'index': [644, 1067, 1641, 1287],
  'loss_amount': 301.4982268130407,
  'loss_min_index': [2,
   3,
   2,
   1,
   2,
   0,
   2,
   1,
   2,
   0,
   0,
   0,
   3,
   3,
   3,
   1,
   2,
   2,
   2,
   1,
   0,
   1,
   0,
   1,
   0,
   2,
   0,
   2,
   0,
   2,
   2,
   0,
   1,
   0,
   2,
   0,
   0,
   0,
   1,
   1,
   0,
   0,
   0,
   1,
   0,
   0,
   1,
   2,
   0,
   1,
   0,
   2,
   2,
   1,
   3,
   0,
   2,
   1,
   2,
   1,
   1,
   1,
   2,
   2,
   2,
   1,
   1,
   1,
   1,
   3,
   1,
   0,
   3,
   1,
   0,
   0,
   2,
   0,
   1,
   1,
   3,
   2,
   2,
   0,
   1,
   0,
   1,
   1,
   1,
   1,
   0,
   0,
   0,
   0,
   1,
   2,
   0,
   1,
   0,
   3,
   1,
   0,
   0,
   0,
   1,
   1,
   3,
   2,
   1,
   0,
   0,
   2,
   0,
   2,
   0,
   0,
   2,
   1,
   2,
   1,
   1,
   2,
   2,
   3,
   1,
   3,
   1,
   0,
   2,
   0,
   1,
   1,
   1,
   1,
   0,
   3,
   1,
   1,
   2,
   1,
   3,
   1,
   0,
   2,
   3,
   0,
   1,
   0,
   0,
   0,
  

In [ ]:
kanji_chars.index('庭')

In [93]:
result_info

{'酔庭爆藍': {'index': [199, 1242, 1584, 774],
  'loss_amount': 306.0336082028225,
  'loss_min_index': [3,
   0,
   0,
   1,
   0,
   2,
   3,
   1,
   0,
   2,
   2,
   2,
   3,
   3,
   1,
   1,
   0,
   0,
   0,
   1,
   2,
   1,
   0,
   1,
   2,
   0,
   2,
   0,
   2,
   0,
   2,
   2,
   3,
   2,
   3,
   2,
   2,
   2,
   0,
   1,
   2,
   2,
   2,
   1,
   2,
   2,
   1,
   0,
   2,
   2,
   2,
   1,
   0,
   1,
   3,
   2,
   1,
   1,
   0,
   1,
   1,
   1,
   0,
   1,
   0,
   1,
   0,
   1,
   1,
   3,
   2,
   2,
   3,
   1,
   2,
   0,
   0,
   2,
   1,
   1,
   1,
   3,
   0,
   2,
   0,
   2,
   0,
   1,
   1,
   0,
   2,
   2,
   2,
   2,
   1,
   0,
   2,
   1,
   2,
   3,
   1,
   2,
   2,
   2,
   1,
   1,
   3,
   0,
   1,
   2,
   2,
   0,
   2,
   0,
   2,
   2,
   0,
   1,
   0,
   1,
   1,
   0,
   0,
   0,
   1,
   3,
   1,
   2,
   0,
   2,
   1,
   1,
   1,
   1,
   1,
   3,
   1,
   1,
   3,
   1,
   3,
   1,
   2,
   0,
   1,
   2,
   1,
   2,
   2,
   2,
   